In [5]:
import os
import numpy as np

import IPython.display as ipd

from pedalboard import Compressor, Gain, Limiter, NoiseGate, Pedalboard, Reverb, Distortion, Delay, time_stretch, PitchShift

import librosa
import numpy as np
import matplotlib.pyplot as plt

import pyloudnorm as pyln

In [6]:
def load_audio_files(dir):
    audio_files = []
    for file in os.listdir(dir):
        if file.endswith(".mp3"):
            audio_files.append(os.path.join("/home/ivanmeresman-higgs/Documents/QueenMary/tracks_for_stage/base tracks/", file))
    return audio_files

sr = 44100

base_track_length_s =60

# load base tracks from /home/ivan/Documents/FIng/QueenMary/
base_tracks_paths = load_audio_files("/home/ivanmeresman-higgs/Documents/QueenMary/tracks_for_stage/base tracks/")
base_tracks = []
for track in base_tracks_paths:
    print(f"Loading {track}...")
    y, _ = librosa.load(track, sr=sr)
    # # cut base song to base_track_length_s
    y = y[:base_track_length_s*sr]
    base_tracks.append(y)

Loading /home/ivanmeresman-higgs/Documents/QueenMary/tracks_for_stage/base tracks/Pop song that has samples in it, in G major.mp3...
Loading /home/ivanmeresman-higgs/Documents/QueenMary/tracks_for_stage/base tracks/edm-song-that-has-samples-in-it-in-g-major_112524.mp3...
Loading /home/ivanmeresman-higgs/Documents/QueenMary/tracks_for_stage/base tracks/Instrumental EDM song that has samples in it, in G major.mp3...
Loading /home/ivanmeresman-higgs/Documents/QueenMary/tracks_for_stage/base tracks/Hip hop song that has samples in it, in G major.mp3...


In [3]:
# ipd.Audio(base_tracks[1], rate=sr)

In [4]:
sample_100_path = "/home/ivan/Documents/FIng/QueenMary/sample_100/"
n_samples = 10

# csv columns are sample_id,original_track_id,sample_track_id,t_original,t_sample,n_repetitions,sample_type,interpolation,comments
# open csv and get t_sample
csv_path = os.path.join(sample_100_path, "samples.csv")

sample_tracks = []
sample_tracks_paths = []
with open(csv_path, encoding="latin-1") as f:
    lines = f.readlines()
    for idx in range(n_samples):
        # t_sample = int(lines[idx + 1].split(",")[4])  # +1 because of header of csv
        track = os.path.join(sample_100_path, "audio", lines[idx + 1].split(",")[1]+".mp3")
        sample_tracks_paths.append(track)
        print(f"Loading {track}...")
        y, _ = librosa.load(track, sr=sr)
        sample_tracks.append(y)


Loading /home/ivan/Documents/FIng/QueenMary/sample_100/audio/T002.mp3...
Loading /home/ivan/Documents/FIng/QueenMary/sample_100/audio/T003.mp3...
Loading /home/ivan/Documents/FIng/QueenMary/sample_100/audio/T003.mp3...
Loading /home/ivan/Documents/FIng/QueenMary/sample_100/audio/T005.mp3...
Loading /home/ivan/Documents/FIng/QueenMary/sample_100/audio/T007.mp3...
Loading /home/ivan/Documents/FIng/QueenMary/sample_100/audio/T010.mp3...
Loading /home/ivan/Documents/FIng/QueenMary/sample_100/audio/T011.mp3...
Loading /home/ivan/Documents/FIng/QueenMary/sample_100/audio/T014.mp3...
Loading /home/ivan/Documents/FIng/QueenMary/sample_100/audio/T015.mp3...
Loading /home/ivan/Documents/FIng/QueenMary/sample_100/audio/T018.mp3...


In [5]:
cfg = {
    "sample_start": {
        "seconds": None, # 0,
        "beats": 24
    },
    "sample_length": {
        "seconds": None, # 5,
        "beats": 16
    },
    "gain": {
        "gain_db": 0 #-3
    },
    "effects":  {
        "compressor": False, #{
        #     "threshold_db": -6,
        #     "ratio": 6,
        #     "attack_ms": 0.001,
        #     "release_ms": 0.2
        # },
        "reverb": False, #{
        #     "room_size": 0.8,
        #     "damping": 0.1,
        #     "wet_level": 0.5,
        #     "dry_level": 0.5
        # },
        "delay": False, #{
            #     "delay_seconds": 0.3,
            #     "feedback": 0.4,
            #     "mix": 0.3
            # },
        "noise_gate": False, #{
        #     "threshold_db": -10,
        #     "attack_ms": 0.001,
        #     "release_ms": 0.1
        # },
        "distortion": False, #{
        #     "drive_db": 20
        # },
        "limiter": False, #{
        #     "threshold_db": -3
        # },
        "noise_gate": False, #{
        #     "threshold_db": -40,
        #     "attack_ms": 0.001,
        #     "release_ms": 0.1
        # },
    },
    "beat_sync": {
        "start_beat": 12, # 0 is the first beat
    },
    "tempo_sync": False, #{
    #     "multiplier": 0.95 # 1 is the original tempo of the base track
    # },
    "tempo_change": 1, # 1 is no change
    "pitch_sync": False, # detects key of the base track and adjusts pitch of sample to match
    "pitch_shift": 0, # in semitones
    "looping": {
        "n_loops": 2, # 1 is no loop
        "loop_every_n_beats": 16
    },
    "masking": False,
}
def effect_sample(sample, sr, cfg):
    assert cfg["gain"] is not None, "Gain is required"
    gain = Gain(gain_db=cfg["gain"]["gain_db"])
    pedalboard = Pedalboard([gain])
    if cfg["effects"]:
        if cfg["effects"]["compressor"]:
            compressor = Compressor(threshold_db=cfg["effects"]["compressor"]["threshold_db"], ratio=cfg["effects"]["compressor"]["ratio"], attack_ms=cfg["effects"]["compressor"]["attack_ms"], release_ms=cfg["effects"]["compressor"]["release_ms"])
            pedalboard.append(compressor)
        if cfg["effects"]["reverb"]:
            reverb = Reverb(room_size=cfg["effects"]["reverb"]["room_size"], damping=cfg["effects"]["reverb"]["damping"], wet_level=cfg["effects"]["reverb"]["wet_level"], dry_level=cfg["effects"]["reverb"]["dry_level"])
            pedalboard.append(reverb)
        # if cfg["effects"]["limiter"]:
        #     limiter = Limiter(threshold_db=cfg["effects"]["limiter"]["threshold_db"])
        #     pedalboard.append(limiter)
        # if cfg["effects"]["noise_gate"]:
        #     noise_gate = NoiseGate(threshold_db=cfg["effects"]["noise_gate"]["threshold_db"], attack_ms=cfg["effects"]["noise_gate"]["attack_ms"], release_ms=cfg["effects"]["noise_gate"]["release_ms"])
        #     pedalboard.append(noise_gate)
        if cfg["effects"]["delay"]:
            delay = Delay(delay_seconds=cfg["effects"]["delay"]["delay_seconds"], feedback=cfg["effects"]["delay"]["feedback"], mix=cfg["effects"]["delay"]["mix"])
            pedalboard.append(delay)
        if cfg["effects"]["distortion"]:
            distortion = Distortion(drive_db=cfg["effects"]["distortion"]["drive_db"])
            pedalboard.append(distortion)

    return pedalboard.process(sample, sr)


def loudness_normalize(y, sr, target_loudness=-12.0):
    # peak_normalized_y = pyln.normalize.peak(y, -1.0)
    meter = pyln.Meter(sr, block_size=0.200) # create BS.1770 meter, default block size is 400ms
    loudness = meter.integrated_loudness(y)
    y = pyln.normalize.loudness(y, loudness, target_loudness)
    return y

In [6]:
# create song by adding sample to base
def create_song(base, sample_source, cfg=None):
    # print(f"Peak value of base: {np.max(base)}, Peak value of sample: {np.max(sample)}")
    sample_tempo, sample_beats = librosa.beat.beat_track(y=sample_source, sr=sr)
    base_tempo, base_beats = librosa.beat.beat_track(y=base, sr=sr)
    assert cfg is not None, "Configuration is required"

    sample_time_annotation = []
    base_time_annotations = []

    # extract sample from source
    print("Extracting sample from sample source...")
    assert cfg["sample_start"] is not None, "Sample start is required"
    assert cfg["sample_length"] is not None, "Sample length is required"
    if cfg["sample_start"]["seconds"] is not None:
        sample_source = sample_source[cfg["sample_start"]["seconds"]*sr:]
        sample_time_annotation.append({"start_time": cfg["sample_start"]["seconds"], "end_time": None})
    elif cfg["sample_start"]["beats"] is not None:
        sample_source = sample_source[librosa.frames_to_samples(sample_beats[cfg["sample_start"]["beats"]]):]
        sample_time_annotation.append({"start_time": librosa.frames_to_time(sample_beats[cfg["sample_start"]["beats"]], sr=sr), "end_time": None})
        sample_beats -= sample_beats[cfg["sample_start"]["beats"]]
    if cfg["sample_length"]["seconds"] is not None:
        sample = sample_source[:cfg["sample_length"]["seconds"]*sr]
        sample_time_annotation[-1]["end_time"] = cfg["sample_length"]["seconds"]
    elif cfg["sample_length"]["beats"] is not None:
        sample = sample_source[:librosa.frames_to_samples(sample_beats[cfg["sample_start"]["beats"]+cfg["sample_length"]["beats"]])]
        sample_time_annotation[-1]["end_time"] = sample_time_annotation[-1]["start_time"] + librosa.frames_to_time(sample_beats[cfg["sample_start"]["beats"]+cfg["sample_length"]["beats"]], sr=sr)
            
    # loudness normalize audio to -12 dB LUFS
    base = loudness_normalize(base, sr, target_loudness=-12.0)
    sample = loudness_normalize(sample, sr, target_loudness=-12.0)
    original_sample = sample

    # half the volume
    gain = Gain(-6)

    board = Pedalboard([gain])

    base = board.process(base, sr)
    sample = board.process(sample, sr)

    # base_start_sample = 0
    pitch_shift_semitones = 0

    # if cfg["masking"]:
    #     # take the signal to silence for n beats
    #     pass

    if cfg["tempo_sync"]:
        stretch_rate = (base_tempo/sample_tempo)[0] * cfg["tempo_sync"]["multiplier"]
        cfg["total_tempo_stretch_rate"] = float(stretch_rate)
        sample = time_stretch(sample, sr, stretch_rate)[0]

    if cfg["tempo_change"] != 1:
        sample = time_stretch(sample, sr, cfg["tempo_change"])[0]

    if cfg["pitch_sync"]:
        sample_chromagram = librosa.feature.chroma_stft(y=sample, sr=sr)
        base_chromagram = librosa.feature.chroma_stft(y=base, sr=sr)
        mean_sample_chroma = np.mean(sample_chromagram, axis=1)
        mean_base_chroma = np.mean(base_chromagram, axis=1)
        sample_estimated_key = np.argmax(mean_sample_chroma)
        base_estimated_key = np.argmax(mean_base_chroma)
        pitch_shift_semitones = base_estimated_key - sample_estimated_key

    if cfg["pitch_shift"]:
        pitch_shift_semitones += cfg["pitch_shift"]

    cfg["total_pitch_shift"] = int(pitch_shift_semitones)

    pitch_shift = Pedalboard([PitchShift(semitones=pitch_shift_semitones)])
    sample = pitch_shift.process(sample, sr)

        
    print("Applying effects to sample...")
    sample = effect_sample(sample, sr, cfg)
    effected_sample = sample

    mix = base
    # mix[:len(sample)] += sample
    assert cfg["looping"] is not None, "Looping configuration is required (even if n_loops=1)"
    start_beat = cfg["beat_sync"]["start_beat"]
    for _ in range(cfg["looping"]["n_loops"]):
        loop_start_sample = librosa.frames_to_samples(base_beats[start_beat])
        mix[loop_start_sample:loop_start_sample+len(sample)] += sample

        start_beat += cfg["looping"]["loop_every_n_beats"]

        base_time_annotations.append({"start_time": librosa.frames_to_time(base_beats[start_beat], sr=sr), "end_time": librosa.frames_to_time(base_beats[start_beat]+librosa.samples_to_frames(len(sample)), sr=sr)})

        if cfg["looping"]["n_loops"] != 1 and cfg["looping"]["loop_every_n_beats"] < cfg["sample_length"]["beats"]:
            print ("Warning: Loops will overlap as sample_length in beats is greater than loop_every_n_beats")

        # # # find closest beat to start_sample
        # start_beat += cfg["looping"]["loop_every_n_beats"]
        # # loop_start_sample = librosa.frames_to_samples(base_beats[end_beat + cfg["looping"]["loop_every_n_beats"]])
        # loop_start_sample = librosa.frames_to_samples(base_beats[start_beat])


    mix[len(sample):] += base[len(sample):]
    # mix[base_start_sample+len(sample):] += base[base_start_sample+len(sample):]

    mix = loudness_normalize(mix, sr, target_loudness=-12.0)

    return mix, original_sample, effected_sample, base_time_annotations, sample_time_annotation, cfg

In [ ]:
import soundfile as sf
import json
# import to save as mp3
import pydub

version = 6

for i, (base, sample) in enumerate(zip(base_tracks[:4], sample_tracks[:8:2])):
    if i != 0 and i != 3:
        pass
    else:
        mix, original_sample, effected_sample, base_time_annotations, sample_time_annotation, cfg = create_song(base, sample, cfg)
        print("====================================")
        print("Original sample")
        ipd.display(ipd.Audio(original_sample, rate=sr))
        print("Sample after processing")
        ipd.display(ipd.Audio(effected_sample, rate=sr))
        print("Mix (final song)")
        ipd.display(ipd.Audio(mix, rate=sr))

        # save mixed audio together with config used
        # save audio as mp3
        sf.write(f"mix_{i}_{i*2}_v{version}.wav", mix, sr)
        # convert to mp3
        sound = pydub.AudioSegment.from_wav(f"mix_{i}_{i*2}_v{version}.wav")
        sound.export(f"mix_{i}_{i*2}_v{version}.mp3", format="mp3")

        # add time annotations to config
        cfg["base_time_annotations"] = base_time_annotations
        cfg["sample_time_annotations"] = sample_time_annotation
        # add file name to config
        cfg["base_file"] = base_tracks_paths[i].split("/")[-1]
        cfg["sample_file"] = sample_tracks_paths[i*2].split("/")[-1]
        # save config
        with open(f"config_{i}_{i*2}_v{version}.json", "w") as f:
            json.dump(cfg, f)

Extracting sample from sample source...
Applying effects to sample...
Original sample


/home/ivan/miniconda3/envs/neural_sample_id/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")
/home/ivan/miniconda3/envs/neural_sample_id/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")
/home/ivan/miniconda3/envs/neural_sample_id/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")


Sample after processing


Mix (final song)


In [ ]:
cfg = {
    "sample_start": {
        "seconds": None, # 0,
        "beats": 24
    },
    "sample_length": {
        "seconds": None, # 5,
        "beats": 16
    },
    "gain": {
        "gain_db": 0
    },
    "effects":  {
        "compressor": False, 
        "reverb": False, 
        "delay": False, 
        "noise_gate": False,
        "distortion": False,
        "limiter": False, 
        "noise_gate": False, 
    },
    "beat_sync": {
        "start_beat": 12, # 0 is the first beat
    },
    "tempo_sync": False, 
    "tempo_change": 1, # 1 is no change
    "pitch_sync": False, # detects key of the base track and adjusts pitch of sample to match
    "pitch_shift": 0, # in semitones
    "looping": {
        "n_loops": 2, # 1 is no loop
        "loop_every_n_beats": 16
    }
}

# [4 suno base tracks (Pop, HipHop/Rap, EDM-instrumental, House-instrumental) + 1 stableAudio base track (EDM-instrumental)] x 10 samples from sample100 sample set (4 drum-based beats, 4 instrumental riffs, 2 with vocals) x 30 augmentations
# = 1500 tracks
config_array = [{'gain': {'gain_db': 0}},
                {'gain': {'gain_db': -3}},
                {'gain': {'gain_db': -6}},
                {'gain': {'gain_db': 1}},
                {"sample_length": {
                    "seconds": None, # 5,
                    "beats": 4
                }},
                {"sample_length": {
                    "seconds": None, # 5,
                    "beats": 8
                }},
                {'tempo_sync': {'multiplier': 1}},
                {'tempo_change': 0.98},
                {'tempo_change': 1.02},
                {'tempo_change': 1.05},
                {'tempo_change': 1.5},
                {'tempo_change': 2},
                {'pitch_sync': True},
                {'pitch_shift': -1},
                {'pitch_shift': 1},
                {'pitch_shift': -3},
                {'pitch_shift': 3},
                {'pitch_shift': -7},
                {'pitch_shift': 7},
                {'pitch_shift': -12},
                {'pitch_shift': 12},
                {'pitch_sync': True, 'tempo_sync': {'multiplier': 1}},
                {'effects': {'compressor': {'threshold_db': -6, 'ratio': 6, 'attack_ms': 0.001, 'release_ms': 0.2}, 'reverb': False, 'delay': False, 'distortion': False}},
                {'effects': {'reverb': {'room_size': 0.8, 'damping': 0.1, 'wet_level': 0.5, 'dry_level': 0.5}, 'compressor': False, 'delay': False, 'distortion': False}},
                {'effects': {'delay': {'delay_seconds': 0.3, 'feedback': 0.4, 'mix': 0.3}, 'compressor': False, 'reverb': False, 'distortion': False}},
                {'effects': {'distortion': {'drive_db': 20},'compressor': False, 'reverb': False, 'delay': False}}, 
                {'effects': {'compressor': {'threshold_db': -6, 'ratio': 6, 'attack_ms': 0.001, 'release_ms': 0.2},
                            'reverb': {'room_size': 0.8, 'damping': 0.1, 'wet_level': 0.5, 'dry_level': 0.5},
                            'delay': {'delay_seconds': 0.3, 'feedback': 0.4, 'mix': 0.3},
                            'distortion': {'drive_db': 20}}
                            },
                {'drums_separation': True},
                {'vocal_separation': True},
                {'bass_separation': True}
                ]

print(f"Creating {len(config_array)*4} songs...")
                
                

Creating 100 songs...


In [8]:
# create folder to save songs
import soundfile as sf
import json
# import to save as mp3
import pydub
import os
os.makedirs(f"artificial_dataset_v1", exist_ok=True)
os.chdir(f"artificial_dataset_v1")
os.makedirs("audio", exist_ok=True)
os.makedirs("audio_wav", exist_ok=True)

version = 0
for config in config_array:
    for i in range(4):
        aux_cfg = cfg.copy()
        aux_cfg.update(config)
        mix, original_sample, effected_sample, base_time_annotations, sample_time_annotation, aux_cfg = create_song(base_tracks[3], sample_tracks[i*2], aux_cfg)

        # save audio together with config used
        
        # save audio as wav
        sf.write(f"audio_wav/mix_{3}_{i*2}_v{version}.wav", mix, sr)
        sf.write(f"audio_wav/original_sample_{3}_{i*2}_v{version}.wav", original_sample, sr)
        sf.write(f"audio_wav/effected_sample_{3}_{i*2}_v{version}.wav", effected_sample, sr)
        # convert to mp3
        sound = pydub.AudioSegment.from_wav(f"audio_wav/mix_{3}_{i*2}_v{version}.wav")
        sound.export(f"audio/mix_{3}_{i*2}_v{version}.mp3", format="mp3")
        sound = pydub.AudioSegment.from_wav(f"audio_wav/original_sample_{3}_{i*2}_v{version}.wav")
        sound.export(f"audio/original_sample_{3}_{i*2}_v{version}.mp3", format="mp3")
        sound = pydub.AudioSegment.from_wav(f"audio_wav/effected_sample_{3}_{i*2}_v{version}.wav")
        sound.export(f"audio/effected_sample_{3}_{i*2}_v{version}.mp3", format="mp3")

        # add time annotations to config
        aux_cfg["base_time_annotations"] = base_time_annotations
        aux_cfg["sample_time_annotations"] = sample_time_annotation
        # add base file name to config
        aux_cfg["base_file"] = base_tracks_paths[3]
        aux_cfg["sample_file"] = sample_tracks_paths[i*2]
        # save config
        with open(f"config_{3}_{i*2}_v{version}.json", "w") as f:
            json.dump(aux_cfg, f)

        print(f"Song {3}_{i*2}_v{version} created!")
    
    version += 1

os.chdir("..")
            


Extracting sample from sample source...
Applying effects to sample...


/home/ivan/miniconda3/envs/neural_sample_id/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")
/home/ivan/miniconda3/envs/neural_sample_id/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")
/home/ivan/miniconda3/envs/neural_sample_id/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")


Song 3_0_v0 created!
Extracting sample from sample source...
Applying effects to sample...


/home/ivan/miniconda3/envs/neural_sample_id/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")
/home/ivan/miniconda3/envs/neural_sample_id/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")
/home/ivan/miniconda3/envs/neural_sample_id/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")


Song 3_2_v0 created!
Extracting sample from sample source...
Applying effects to sample...


...

Song 3_4_v24 created!
Extracting sample from sample source...


/home/ivan/miniconda3/envs/neural_sample_id/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")
/home/ivan/miniconda3/envs/neural_sample_id/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")


Applying effects to sample...


/home/ivan/miniconda3/envs/neural_sample_id/lib/python3.12/site-packages/pyloudnorm/normalize.py:62: UserWarning: Possible clipped samples in output.
  warnings.warn("Possible clipped samples in output.")


Song 3_6_v24 created!


In [ ]:

os.chdir("..")
